# Colonne virtuali

In [1]:
from gnr.app.gnrapp import GnrApp

#istanzio oggetto GnrApp passando il nome dell'istanza di sandbox chiamata sandboxpg
app = GnrApp('sandboxpg')
#dell'oggetto GnrApp mi interessa al momento solo il puntatore all'oggetto GnrSqlDb  
#questo è il mapper corrispondente dal database dell'applicazione
mydb = app.db
#prendo la table cliente
tbl_cliente = mydb.table('fatt.cliente')

In [3]:
#questa è una query sulla table cliente. Vorrei semplificare la lettura delle colonne in relazione
rel_query = tbl_cliente.query(columns='$ragione_sociale,@provincia.nome AS nome_provincia', 
                              where='@provincia.regione = :reg',
                              reg='LOM',
                              limit=5)
rel_query.fetch()

[[ragione_sociale=Effelunga,nome_provincia=Milano,pkey=eXTjroRqOLqqaP5Ez4vL0g],
 [ragione_sociale=Bianchi Luigino,nome_provincia=Milano,pkey=pN1YrXqfPyinfCQBQ2qewQ],
 [ragione_sociale=Giardini e Giardini,nome_provincia=Milano,pkey=ja14mgX2P2mRQWUNMWcdKg],
 [ragione_sociale=Mario Rossi,nome_provincia=Milano,pkey=syd9_cQZPm_AxELj3jJKxw],
 [ragione_sociale=Porcari Francesco,nome_provincia=Milano,pkey=g8pa8wDvMIeQW0R8Chn6ZA]]

## Alias columns


tbl.aliasColumn('provincia_nome', relation_path='@provincia.nome', name_long='Nome provincia')
 
 
tbl.aliasColumn('regione_sigla', relation_path='@provincia.regione', name_long='Regione sigla')


tbl.aliasColumn('regione_nome', relation_path='@provincia.@regione.nome', name_long='Regione nome')
        

In [2]:
tbl_cliente.model.virtual_columns.keys()


['__protecting_reasons',
 '__is_protected_row',
 '__invalid_reasons',
 '__is_invalid_row',
 'rsociale_upper',
 'etichetta',
 'n_fatture',
 'tot_fatturato',
 'provincia_nome',
 'regione_sigla',
 'regione_nome',
 'zona',
 'provv_calc',
 '__allowed_for_partition']

In [6]:
rel_query = tbl_cliente.query(columns='$ragione_sociale,$provincia_nome',
                                      where='$regione_sigla = :reg',
                                      reg='LOM',
                                      limit=5)
#rel_query.fetch()
print(rel_query.sqltext)

SELECT  t0."ragione_sociale" AS "ragione_sociale",
t1."nome" AS "provincia_nome",
t0.id AS pkey
 FROM fatt."fatt_cliente" AS t0
       LEFT JOIN glbl."glbl_provincia" AS t1 ON t1."sigla" = t0."provincia"
WHERE  ( t0.__del_ts IS NULL ) AND ( t1."regione" = :reg ) 
LIMIT 5


In [3]:
tbl_cliente.query(columns="$etichetta", order_by='LENGTH($ragione_sociale) DESC').fetch()

[[etichetta=BERLUCCHI SANDIONIGI ALBERTO - Nord-ovest,pkey=z5zL6h_hMNeZmVK6IRqpIA],
 [etichetta=GIARDINI E GIARDINI - Nord-ovest,pkey=ja14mgX2P2mRQWUNMWcdKg],
 [etichetta=ROSSINI GIOACCHINO - Centro,pkey=GLnTrBCJNbSDR_ksdSgCwA],
 [etichetta=ROCKERDUCK S.P.A. - Nord-est,pkey=OyEArIUTNdKfqOUNt9yHeA],
 [etichetta=PORCARI FRANCESCO - Nord-ovest,pkey=g8pa8wDvMIeQW0R8Chn6ZA],
 [etichetta=PORTACCO GESUINO - Isole,pkey=YtQO9zvkPtKxYNNAnndbbQ],
 [etichetta=BIANCHI ROBERTO - Centro,pkey=hbKT6g9mPUGrWPAaPZ3kVg],
 [etichetta=PUCCINI GIACOMO - Centro,pkey=oMR8MXV_PNuo_SUYIqVDpQ],
 [etichetta=BIANCHI LUIGINO - Nord-ovest,pkey=pN1YrXqfPyinfCQBQ2qewQ],
 [etichetta=PUCCINI GIACOMO - Centro,pkey=IFIE_rmrMOqIHaAj8HrEOg],
 [etichetta=CAMILLOZZI SPA - Nord-ovest,pkey=huWxufwWNqeERsBSbHiXbw],
 [etichetta=GOTTARI MARISA - Nord-est,pkey=M519McwOPZaBESOycDaTEQ],
 [etichetta=GALIMBERTI SRL - Nord-est,pkey=zWWqpVSiMASzjnkhyoBcEw],
 [etichetta=SETTORALIA SRL - Nord-est,pkey=Ixr_V71QMf6KNV7MUqs3Cw],
 [etichetta=VE

## FormulaColumns

tbl.formulaColumn('n_fatture',select=dict(table='fatt.fattura',
                                                  columns='COUNT(*)',
                                                  where='$cliente_id=#THIS.id'),
                                                  dtype='L',name_long='N.Fatture')

tbl.formulaColumn('tot_fatturato',select=dict(table='fatt.fattura',
                                                  columns='SUM($totale_fattura)',
                                                  where='$cliente_id=#THIS.id'),
                                                  dtype='N',name_long='Tot.Fatturato')

In [5]:
q_formula = tbl_cliente.query(columns='$etichetta,$n_fatture,$fatt_avg', where='$n_fatture > :n', n=5, order_by='$n_fatture DESC')

In [6]:
print(q_formula.sqltext)

SELECT  ( ( UPPER(t0."ragione_sociale") ) ||' - '|| t2."zona" ) AS "etichetta",
(  ( SELECT  COUNT(*) AS "COUNT___"
 FROM fatt."fatt_fattura" AS t0_t0
WHERE t0_t0."cliente_id"=t0."id" )  ) AS "n_fatture",
( (CASE WHEN (  ( SELECT  COUNT(*) AS "COUNT___"
 FROM fatt."fatt_fattura" AS t0_t0
WHERE t0_t0."cliente_id"=t0."id" )  ) >0 
                                                    THEN (  ( SELECT  SUM(t0_t0."totale_fattura") AS "SUM__totale_fattura_"
 FROM fatt."fatt_fattura" AS t0_t0
WHERE t0_t0."cliente_id"=t0."id" )  ) / (  ( SELECT  COUNT(*) AS "COUNT___"
 FROM fatt."fatt_fattura" AS t0_t0
WHERE t0_t0."cliente_id"=t0."id" )  ) 
                                               ELSE  0 END) ) AS "fatt_avg",
t0.id AS pkey
 FROM fatt."fatt_cliente" AS t0
       LEFT JOIN glbl."glbl_provincia" AS t1 ON t1."sigla" = t0."provincia"
       LEFT JOIN glbl."glbl_regione" AS t2 ON t2."sigla" = t1."regione"
WHERE  ( t0.__del_ts IS NULL ) AND ( (  ( SELECT  COUNT(*) AS "COUNT___"
 FROM fatt."fatt

In [7]:
q_formula.fetch()

[[etichetta=BIANCHI ROBERTO - Centro,n_fatture=31,fatt_avg=713.3431612903225806,pkey=hbKT6g9mPUGrWPAaPZ3kVg],
 [etichetta=GALIMBERTI SRL - Nord-est,n_fatture=30,fatt_avg=5812.6389333333333333,pkey=zWWqpVSiMASzjnkhyoBcEw],
 [etichetta=ROSSINI GIOACCHINO - Centro,n_fatture=29,fatt_avg=531.6244827586206897,pkey=GLnTrBCJNbSDR_ksdSgCwA],
 [etichetta=BERLUCCHI SANDIONIGI ALBERTO - Nord-ovest,n_fatture=25,fatt_avg=774.5645600000000000,pkey=z5zL6h_hMNeZmVK6IRqpIA],
 [etichetta=EFFELUNGA - Nord-ovest,n_fatture=24,fatt_avg=35420.020000000000,pkey=eXTjroRqOLqqaP5Ez4vL0g],
 [etichetta=PORTACCO GESUINO - Isole,n_fatture=24,fatt_avg=716.7008333333333333,pkey=YtQO9zvkPtKxYNNAnndbbQ],
 [etichetta=ROCKERDUCK S.P.A. - Nord-est,n_fatture=24,fatt_avg=53495.873333333333,pkey=OyEArIUTNdKfqOUNt9yHeA],
 [etichetta=ROSSI MARIO - Nord-ovest,n_fatture=22,fatt_avg=760.2725454545454545,pkey=mf_6EJbWN1unRWkVjRRTgA],
 [etichetta=BIANCHI LUIGINO - Nord-ovest,n_fatture=22,fatt_avg=861.9331818181818182,pkey=pN1YrXqfPyi